# How to create a project

This tutorial demonstrates how to create a project.

## What is a project?

A project is a speos simulation container that includes parts, material properties, sensor,
sources and simulations.

In this tutorial you will learn how to create a project from scratch or from a pre-defined .speos
file.

In [1]:
import os
from pathlib import Path

from ansys.speos.core import Project, Speos
from ansys.speos.core.sensor import SensorIrradiance
from ansys.speos.core.simulation import SimulationDirect
from ansys.speos.core.source import SourceLuminaire, SourceSurface

# If using docker container
assets_data_path = Path("/app") / "assets"
# If using local server
# assets_data_path = Path().resolve().parent.parent / "tests" / "assets"
# If using a different path
# assets_data_path = Path("path/to/downloaded/example/assets")

## Create connection with speos rpc server

In [2]:
speos = Speos(host="localhost", port=50098)

## New empty project

An empty project can be created by only passing speos rpc server to the Project class.

In [3]:
p = Project(speos=speos)
print(p)

{
    "name": "",
    "description": "",
    "metadata": {},
    "part_guid": "",
    "sources": [],
    "sensors": [],
    "simulations": [],
    "materials": [],
    "scenes": []
}


create feature - e.g. source

In [4]:
source1 = p.create_source(name="Source.1", feature_type=SourceLuminaire)
source1.set_intensity_file_uri(uri=str(assets_data_path / "IES_C_DETECTOR.ies"))
source1.commit()

create feature - e.g. sensor

In [5]:
sensor1 = p.create_sensor(name="Sensor.1")
sensor1.commit()

create feature - e.g. optical property

In [6]:
opt_prop1 = p.create_optical_property(name="Material.1")
opt_prop1.commit()

## Read Project

User can read the content of a project via simplily printing the project

In [7]:
print(p)

{
    "sources": [
        {
            "name": "Source.1",
            "metadata": {
                "UniqueId": "1b5f9863-c0f0-48c5-a5cd-dab9482d216a"
            },
            "source_guid": "b30db624-53f2-4672-b68b-a240ace73ab9",
            "description": "",
            "source": {
                "name": "Source.1",
                "luminaire": {
                    "flux_from_intensity_file": {},
                    "intensity_file_uri": "/app/assets/IES_C_DETECTOR.ies",
                    "spectrum_guid": "da5f907d-5ea4-4d00-a092-0f96077dcbe6",
                    "spectrum": {
                        "name": "Source.1.Spectrum",
                        "predefined": {
                            "incandescent": {}
                        },
                        "description": "",
                        "metadata": {}
                    },
                    "axis_system": [
                        0.0,
                        0.0,
                        0.0,
       

Or, user can use the find_key method to read a specific feature:

In [8]:
for it in p.find_key(key="monochromatic"):
    print(it)

## Find a feature inside a project

### Use find method with an exact name

If no feature is found, an empty list is returned.

In [9]:
features = p.find(name="UnexistingName")
print(features)

[]


In [10]:
features = p.find(name="Sensor.1")
print(features[0])

{
    "name": "Sensor.1",
    "metadata": {
        "UniqueId": "258cd231-6950-4b83-b181-7a4add36efbf"
    },
    "sensor_guid": "d83932bd-7fed-484a-a0ff-58d1dcc7b87d",
    "description": "",
    "result_file_name": "",
    "sensor": {
        "irradiance_sensor_template": {
            "sensor_type_photometric": {},
            "illuminance_type_planar": {},
            "dimensions": {
                "x_start": -50.0,
                "x_end": 50.0,
                "x_sampling": 100,
                "y_start": -50.0,
                "y_end": 50.0,
                "y_sampling": 100
            },
            "axis_system": [
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
                0.0,
                0.0,
                1.0
            ],
            "layer_type_none": {},
            "ray_file_type": "RayFileNone",
            "integrati

### Use find method with feature type

Here a wrong type is given: no source is called Sensor.1 in the project

In [11]:
features = p.find(name="Sensor.1", feature_type=SourceLuminaire)
print(features)

[]


In [12]:
features = p.find(name="Sensor.1", feature_type=SensorIrradiance)
print(features[0])

{
    "name": "Sensor.1",
    "metadata": {
        "UniqueId": "258cd231-6950-4b83-b181-7a4add36efbf"
    },
    "sensor_guid": "d83932bd-7fed-484a-a0ff-58d1dcc7b87d",
    "description": "",
    "result_file_name": "",
    "sensor": {
        "irradiance_sensor_template": {
            "sensor_type_photometric": {},
            "illuminance_type_planar": {},
            "dimensions": {
                "x_start": -50.0,
                "x_end": 50.0,
                "x_sampling": 100,
                "y_start": -50.0,
                "y_end": 50.0,
                "y_sampling": 100
            },
            "axis_system": [
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
                0.0,
                0.0,
                1.0
            ],
            "layer_type_none": {},
            "ray_file_type": "RayFileNone",
            "integrati

### Use find method with approximation name with regex

find a feature with name starting with Mat

In [13]:
features = p.find(name="Mat.*", name_regex=True)
for feat in features:
    print(str(type(feat)) + " : name=" + feat._name)

<class 'ansys.speos.core.opt_prop.OptProp'> : name=Material.1


find all features without defining any name

In [14]:
features = p.find(name=".*", name_regex=True)
for feat in features:
    print(str(type(feat)) + " : name=" + feat._name)

<class 'ansys.speos.core.source.SourceLuminaire'> : name=Source.1
<class 'ansys.speos.core.sensor.SensorIrradiance'> : name=Sensor.1
<class 'ansys.speos.core.opt_prop.OptProp'> : name=Material.1


## Delete

This erases the scene content in server database.

This deletes also each feature of the project

In [15]:
p.delete()
print(p)

{
    "name": "",
    "description": "",
    "metadata": {},
    "part_guid": "",
    "sources": [],
    "sensors": [],
    "simulations": [],
    "materials": [],
    "scenes": []
}


As the features were deleted just above -> this returns an empty vector

In [16]:
print(p.find(name="Sensor.1"))

[]


## Create project from pre-defined speos project

Via passing the .speos/.sv5 file path to the Project class.

In [17]:
p2 = Project(
    speos=speos,
    path=str(assets_data_path / "LG_50M_Colorimetric_short.sv5" / "LG_50M_Colorimetric_short.sv5"),
)
print(p2)

{
    "name": "LG_50M_Colorimetric_short",
    "description": "From /app/assets/LG_50M_Colorimetric_short.sv5/LG_50M_Colorimetric_short.sv5",
    "part_guid": "32aa2337-7d3e-4f41-b31f-5082b7f365dc",
    "sources": [
        {
            "name": "Dom Source 2 (0) in SOURCE2",
            "metadata": {
                "UniqueId": "6f9b0315-7293-4f83-827c-4e1c0f4fa1d6"
            },
            "source_guid": "a8392277-d667-4f09-91e1-39d8e9842dac",
            "description": "",
            "source": {
                "name": "Dom Source 2 (0) in SOURCE2",
                "surface": {
                    "radiant_flux": {
                        "radiant_value": 6.590041607465698
                    },
                    "intensity_guid": "c6561a84-3c10-4af6-b321-6eed76b8de53",
                    "exitance_constant": {
                        "geo_paths": [
                            {
                                "geo_path": "Solid Body in SOURCE2:2920204960/Face in SOURCE2:222",

## Preview the part information

User can check the project part using preview method.

In [18]:
p2.preview()

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

use find_key method to find specific information

In [19]:
for it in p2.find_key(key="surface"):
    print(it)

(".sources[.name='Dom Source 2 (0) in SOURCE2'].source.surface", {'radiant_flux': {'radiant_value': 6.590041607465698}, 'intensity_guid': 'c6561a84-3c10-4af6-b321-6eed76b8de53', 'exitance_constant': {'geo_paths': [{'geo_path': 'Solid Body in SOURCE2:2920204960/Face in SOURCE2:222', 'reverse_normal': False}]}, 'spectrum_guid': 'c5906c39-d431-446b-87e1-d2f6618e1c07', 'intensity': {'cos': {'N': 1.0, 'total_angle': 180.0}, 'name': '', 'description': '', 'metadata': {}}, 'spectrum': {'library': {'file_uri': '/app/assets/LG_50M_Colorimetric_short.sv5/Red Spectrum.spectrum'}, 'name': '', 'description': '', 'metadata': {}}})
(".sources[.name='Surface Source (0) in SOURCE1'].source.surface", {'radiant_flux': {'radiant_value': 9.290411220389682}, 'intensity_guid': '6216f59b-8b47-422f-ab67-d9de63e551aa', 'exitance_constant': {'geo_paths': [{'geo_path': 'Solid Body in SOURCE1:2494956811/Face in SOURCE1:187', 'reverse_normal': False}]}, 'spectrum_guid': 'a8cc47a4-36a5-4f62-ad3c-42335b99a658', 'inte

Use find method to retrieve feature:

e.g. surface source

In [20]:
features = p2.find(name=".*", name_regex=True, feature_type=SourceSurface)
print(features)
for feat in features:
    print(str(type(feat)) + " : name=" + feat._name)
src = features[1]

[<ansys.speos.core.source.SourceSurface object at 0x7fda735beec0>, <ansys.speos.core.source.SourceSurface object at 0x7fda735bf6a0>]
<class 'ansys.speos.core.source.SourceSurface'> : name=Dom Source 2 (0) in SOURCE2
<class 'ansys.speos.core.source.SourceSurface'> : name=Surface Source (0) in SOURCE1


modify the surface source, e.g. surface source wavelength:

In [21]:
src.set_spectrum().set_monochromatic(wavelength=550)
src.commit()

Retrieve a simulation feature:

In [22]:
features = p2.find(name=".*", name_regex=True, feature_type=SimulationDirect)
sim_feat = features[0]
print(sim_feat)

{
    "name": "ASSEMBLY1.DS (0)",
    "metadata": {
        "UniqueId": "35b99e01-6e0f-4090-83a4-f1e882ac0015"
    },
    "simulation_guid": "f30b4f88-1b3d-4782-9bf9-63d85504e543",
    "sensor_paths": [
        "Dom Irradiance Sensor (0)"
    ],
    "source_paths": [
        "Dom Source 2 (0) in SOURCE2",
        "Surface Source (0) in SOURCE1"
    ],
    "description": "",
    "simulation": {
        "direct_mc_simulation_template": {
            "geom_distance_tolerance": 0.05,
            "max_impact": 100,
            "weight": {
                "minimum_energy_percentage": 0.005
            },
            "dispersion": true,
            "colorimetric_standard": "CIE_1931",
            "fast_transmission_gathering": false,
            "ambient_material_uri": ""
        },
        "name": "ASSEMBLY1.DS (0)",
        "metadata": {},
        "description": "",
        "scene_guid": "7ffa7f3a-e025-40cf-9be4-02bc4ae0f5f2",
        "simulation_path": "ASSEMBLY1.DS (0)",
        "job_type

In [23]:
sim_feat.compute_CPU()

[upload_response {
  info {
    uri: "2f11ecbd-5677-44bf-bf17-bac88564f8ac"
    file_name: "ASSEMBLY1.DS (0).Dom Irradiance Sensor (0).xmp"
    file_size: 1477091
  }
  upload_duration {
    nanos: 2240817
  }
}
, upload_response {
  info {
    uri: "e58a9fb0-ec04-403b-879a-103dc11a9011"
    file_name: "ASSEMBLY1.DS (0).html"
    file_size: 496010
  }
  upload_duration {
    nanos: 787752
  }
}
]

Preview simulation result (only windows)

In [24]:
if os.name == "nt":
    from ansys.speos.core.workflow.open_result import open_result_image

    open_result_image(
        simulation_feature=sim_feat,
        result_name="ASSEMBLY1.DS (0).Dom Irradiance Sensor (0).xmp",
    )